<a href="https://colab.research.google.com/github/yaswhar/learning-genesis-sim/blob/main/Hybrid%20Robot.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install genesis-world -q
!pip install mediapy -q

In [ ]:
import os
NVIDIA_ICD_CONFIG_PATH = '/usr/share/glvnd/egl_vendor.d/10_nvidia.json'
ICD_CONFIG_CONTENT = """{
    "file_format_version" : "1.0.0",
    "ICD" : {
        "library_path" : "libEGL_nvidia.so.0"
    }
}
"""
with open(NVIDIA_ICD_CONFIG_PATH, 'w') as f:
    f.write(ICD_CONFIG_CONTENT)

In [ ]:
import genesis as gs
import numpy as np
import torch
import mediapy as media
from tqdm.notebook import tqdm

In [ ]:
gs.init(seed=0, precision='32', logging_level='debug')

[Genesis] [23:49:36] [INFO] ╭───────────────────────────────────────────────╮
INFO:genesis:~<╭───────────────────────────────────────────────╮>~
[Genesis] [23:49:36] [INFO] │┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈ Genesis ┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈│
INFO:genesis:~<│┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈>~ ~~~~<Genesis>~~~~ ~<┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈│>~
[Genesis] [23:49:36] [INFO] ╰───────────────────────────────────────────────╯
INFO:genesis:~<╰───────────────────────────────────────────────╯>~
[Genesis] [23:49:36] [INFO] Running on [Tesla T4] with backend gs.cuda. Device memory: 14.74 GB.
INFO:genesis:Running on ~~<[Tesla T4]>~~ with backend ~~<gs.cuda>~~. Device memory: ~~<14.74>~~ GB.
[Genesis] [23:49:37] [DEBUG] [Taichi] version 1.7.3, llvm 15.0.4, commit 5ec301be, linux, python 3.11.11
DEBUG:genesis:[Taichi] version 1.7.3, llvm 15.0.4, commit 5ec301be, linux, python 3.11.11
[Genesis] [23:49:37] [DEBUG] [Taichi] Starting on arch=cuda
DEBUG:genesis:[Taichi] Starting on arch=cuda
[Genesis] [23:49:37] [INFO] 🚀 Genesis initialized. 🔖 v

In [ ]:
# Create Scene

dt = 3e-3
scene = gs.Scene(
    sim_options=gs.options.SimOptions(
        substeps=10,
    ),
    viewer_options= gs.options.ViewerOptions(
        camera_pos=(1.5, 1.3, 0.5),
        camera_lookat=(0.0, 0.0, 0.0),
        camera_fov=40,
    ),
    rigid_options=gs.options.RigidOptions(
        dt=dt,
        gravity=(0, 0, -9.8),
        enable_collision=True,
        enable_self_collision=False,
        contact_resolve_time=0.02,
        # avoid the rigid contact solver being too stiff otherwise will cause large impulse (especially we have small dt for rigid solver)
    ),
    mpm_options=gs.options.MPMOptions(
        dt=dt,
        lower_bound=( 0.0,  0.0, -0.2),
        upper_bound=( 1.0,  1.0,  1.0),
        gravity=(0, 0, 0), # mimic gravity compensation
        enable_CPIC=True,
    ),
    vis_options=gs.options.VisOptions(
        show_world_frame=True,
        visualize_mpm_boundary=False,
    ),
    show_viewer = False,
)

cam = scene.add_camera(
    res    = (640, 480),
    pos    = (1.5, 1.3, 0.5),
    lookat = (0, 0, 0),
    fov    = 40,
    GUI    = False,
)

[Genesis] [23:49:38] [INFO] Scene <b1b3b51> created.
INFO:genesis:Scene ~~~<<b1b3b51>>~~~ created.


In [ ]:
# Add Entities

scene.add_entity(morph=gs.morphs.Plane())

robot = scene.add_entity(
    morph=gs.morphs.URDF(
        file="urdf/simple/two_link_arm.urdf",
        pos=(0.5, 0.5, 0.3),
        euler=(0.0, 0.0, 0.0),
        scale=0.2,
        fixed=True,
    ),
    material=gs.materials.Hybrid(
        mat_rigid=gs.materials.Rigid(
            gravity_compensation=1.,
        ),
        mat_soft=gs.materials.MPM.Muscle( # to allow setting group
            E=1e4,
            nu=0.45,
            rho=1000.,
            model='neohooken',
        ),
        thickness=0.05,
        damping=1000.,
        func_instantiate_rigid_from_soft=None,
        func_instantiate_soft_from_rigid=None,
        func_instantiate_rigid_soft_association=None,
    ),
)

ball = scene.add_entity(
    morph=gs.morphs.Sphere(
        pos=(0.8, 0.6, 0.1),
        radius=0.1,
    ),
    material=gs.materials.Rigid(rho=1000, friction=0.5),
)


[Genesis] [23:49:38] [INFO] Adding <gs.RigidEntity>. idx: 0, uid: <524451e>, morph: <gs.morphs.Plane>, material: <gs.materials.Rigid>.
INFO:genesis:Adding ~<<gs.RigidEntity>>~. idx: ~<0>~, uid: ~~~<<524451e>>~~~, morph: ~<<gs.morphs.Plane>>~, material: ~<<gs.materials.Rigid>>~.
[Genesis] [23:49:38] [DEBUG] Preprocessed `.gsd` file found in cache for geom idx 0.
DEBUG:genesis:Preprocessed `.gsd` file found in cache for geom idx 0.
[Genesis] [23:49:38] [INFO] Adding <gs.HybridEntity>. idx: 1, uid: <2a54e07>, morph: <gs.morphs.URDF(file='/usr/local/lib/python3.11/dist-packages/genesis/assets/urdf/simple/two_link_arm.urdf')>, material: <gs.materials.Hybrid>.
INFO:genesis:Adding ~<<gs.HybridEntity>>~. idx: ~<1>~, uid: ~~~<<2a54e07>>~~~, morph: ~<<gs.morphs.URDF(file='/usr/local/lib/python3.11/dist-packages/genesis/assets/urdf/simple/two_link_arm.urdf')>>~, material: ~<<gs.materials.Hybrid>>~.
[Genesis] [23:49:38] [INFO] Use default coupling in hybrid. Overwrite `needs_coup` in rigid materia

In [ ]:
# Build
scene.build()

[Genesis] [23:49:38] [INFO] Building scene <b1b3b51>...
INFO:genesis:Building scene ~~~<<b1b3b51>>~~~...
[Genesis] [23:49:45] [WARNING] Kernel compilation takes longer when running MPM solver in CPIC mode. Please be patient.
[Genesis] [23:49:45] [INFO] Compiling simulation kernels...
INFO:genesis:Compiling simulation kernels...


In [ ]:
# Run

scene.reset()
frames = []
for i in range(1000):
    dofs_ctrl = np.array([
        1. * np.sin(2 * np.pi * i * 0.001),
    ] * robot.n_dofs)

    robot.control_dofs_velocity(dofs_ctrl)

    scene.step()
    frames.append(cam.render()[0])

[Genesis] [23:50:22] [INFO] Resetting Scene <b1b3b51>.
INFO:genesis:Resetting Scene ~~~<<b1b3b51>>~~~.
[Genesis] [23:50:22] [INFO] Running at 195.34 FPS.
INFO:genesis:Running at ~<195.34>~ FPS.
[Genesis] [23:50:23] [INFO] Running at 63.26 FPS.
INFO:genesis:Running at ~<63.26>~ FPS.
[Genesis] [23:50:23] [INFO] Running at 59.85 FPS.
INFO:genesis:Running at ~<59.85>~ FPS.
[Genesis] [23:50:23] [INFO] Running at 57.09 FPS.
INFO:genesis:Running at ~<57.09>~ FPS.
[Genesis] [23:50:23] [INFO] Running at 53.99 FPS.
INFO:genesis:Running at ~<53.99>~ FPS.
[Genesis] [23:50:23] [INFO] Running at 50.87 FPS.
INFO:genesis:Running at ~<50.87>~ FPS.
[Genesis] [23:50:23] [INFO] Running at 49.18 FPS.
INFO:genesis:Running at ~<49.18>~ FPS.
[Genesis] [23:50:23] [INFO] Running at 46.77 FPS.
INFO:genesis:Running at ~<46.77>~ FPS.
[Genesis] [23:50:23] [INFO] Running at 44.72 FPS.
INFO:genesis:Running at ~<44.72>~ FPS.
[Genesis] [23:50:23] [INFO] Running at 42.85 FPS.
INFO:genesis:Running at ~<42.85>~ FPS.
[Gene

In [ ]:
media.show_video(frames, fps=100)

This browser does not support the video tag.
